# Practica IA

En esta practica, trataremos de crear un chatbot que transcriba los audios de voz a texto, vamos a fine tunear un modelo de Open AI para realizar este tipo de trabajo.
Por ello, para empezar, cargaremos las librerias necesarias:

In [4]:
!pip install --upgrade pip
!pip install --upgrade datasets[audio] transformers accelerate evaluate jiwer tensorboard gradio


Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


Loggearemos en Hugging Face para poder bajar el dataset

In [ ]:
from huggingface_hub import login

# Reemplaza "tu_token" con tu token de Hugging Face
login("Ingresar token")

Dado a que el dataset tiene un peso relativamente grande, no es posible trabajarlo desde el colab, por ello lo trabajaremos desde un entorno local, sin embargo, cargaremos los datos en streaming para no tener inconvenientes por el uso de espacio en disco.

El dataset utilizado es common voice de Mozzilla foundation, se disponible en varios idiomas pero nosotros utilizaremos el idioma español.
Sin embargo, solo se van a utilizar 1300 ejemplos del dataset en train, validation y test, debido a que no es importante una clasificacion interna de los valores ya que son para entrenamiento y la fuente de donde se obtuvo es una fuente confiable, entonces procedemos a trabajar directamente con ellos. 

In [26]:
from datasets import load_dataset, DatasetDict, concatenate_datasets, Dataset

common_voice = DatasetDict()

# Load 'train' and 'validation' splits separately in streaming mode
train_dataset = load_dataset(
    "mozilla-foundation/common_voice_11_0",
    "es",
    split="train",
    streaming=True,
    trust_remote_code=True
).take(500)
validation_dataset = load_dataset(
    "mozilla-foundation/common_voice_11_0",
    "es",
    split="validation",
    streaming=True,
    trust_remote_code=True
).take(500)

# Convert IterableDatasets to Datasets
train_dataset = Dataset.from_list(list(train_dataset)) # Convert to regular Dataset
validation_dataset = Dataset.from_list(list(validation_dataset)) # Convert to regular Dataset


# Concatenate the 'train' and 'validation' splits into a single 'train' split
common_voice["train"] = concatenate_datasets([train_dataset, validation_dataset])

common_voice["test"] = load_dataset(
    "mozilla-foundation/common_voice_11_0",
    "es",
    split="test",
    streaming=True,
    trust_remote_code=True
).take(300)
common_voice["test"] = Dataset.from_list(list(common_voice["test"])) # Convert to regular Dataset

# Now you can iterate over the dataset without loading it fully into memory
for example in common_voice["train"]:
    print(example)
    break  # Only show the first example to avoid iterating over the entire dataset

Reading metadata...: 230467it [00:05, 39698.86it/s]
Reading metadata...: 15520it [00:00, 18429.16it/s]
Reading metadata...: 15520it [00:00, 55018.70it/s]


{'client_id': '34719bb7c7344da7733b85c9d7215d24326093f1a2cd3a445bdc6dfe9ec4a8c9fe9729a73f6c29764545276bff81ffa65d3944f6da7a3ee3c06d0eb124fac797', 'path': 'es_train_0/common_voice_es_18338585.mp3', 'audio': {'array': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0

Procedemos a eliminar las columnas que no son necesarias en este caso para nuestro entrenamiento del modelo

In [27]:
# Lista de columnas a eliminar
columns_to_remove = ["accent", "age", "client_id", "down_votes", "gender", "locale", "path", "segment", "up_votes"]

# Eliminar columnas directamente
common_voice = common_voice.remove_columns(columns_to_remove)

print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 1000
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 300
    })
})


Cargamos el modelo Whisper-small para hacer un finetuneado con el dataset que hemos cargado.

In [11]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Spanish", task="transcribe")


Verificamos que se hayan cargado valores del dataset

In [12]:
audio_data = common_voice["train"][0]['audio']
print(f"Tipo de audio: {type(audio_data)}")
print(f"Claves de audio: {audio_data.keys()}")
print(f"Tamaño del array de audio: {len(audio_data['array'])} muestras")
print(f"Tasa de muestreo: {audio_data['sampling_rate']} Hz")


Tipo de audio: <class 'dict'>
Claves de audio: dict_keys(['array', 'path', 'sampling_rate'])
Tamaño del array de audio: 217728 muestras
Tasa de muestreo: 48000 Hz


Importamos la funcion audio para poder trabajar con el dataset

In [28]:
from datasets import Audio

common_voice = common_voice.cast_column("audio", Audio(sampling_rate=16000))


In [29]:
print(common_voice["train"][0])


{'audio': {'path': None, 'array': array([ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
        2.06304503e-06, -1.93879605e-05, -3.51465824e-05]), 'sampling_rate': 16000}, 'sentence': '¿ Qué tal a tres de cinco ?'}


Procedemos a realizar una funcion de preprocesado para los valores del dataset de acuerdo a la informacion proporcionada por los desarrolladores del mismo.

In [30]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer

# Cargar el feature extractor y tokenizer de Whisper
feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")
tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small")

def prepare_dataset(batch, feat_ext, tok):
    audio = batch["audio"]
    # Compute log-Mel input features from input audio array
    batch["input_features"] = feat_ext(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    # Encode target text to label ids
    batch["labels"] = tok(batch["sentence"]).input_ids
    return batch

# Aplicar la función al dataset pasando las variables como argumentos
common_voice = common_voice.map(
    prepare_dataset,
    remove_columns=common_voice.column_names["train"],
    num_proc=4,
    fn_kwargs={"feat_ext": feature_extractor, "tok": tokenizer}
)


Map (num_proc=4): 100%|██████████| 300/300 [00:17<00:00, 17.13 examples/s]


In [31]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")


In [32]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [33]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)


Procedemos a evaluar de acuerdo a la metrica World Error Rate (WER) 

In [34]:
import evaluate

metric = evaluate.load("wer")


In [35]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [36]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-small-practica",  # change to a repo name of your choice
    per_device_train_batch_size=2,
    gradient_accumulation_steps=8,  # increase by 2x for every 2x decrease in batch size
    learning_rate=2e-5,
    warmup_steps=500,
    max_steps=200,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=100,
    eval_steps=100,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)


C:\Users\Santiago\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.13_qbz5n2kfra8p0\LocalCache\local-packages\Python313\site-packages\transformers\training_args.py:1594: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [37]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=common_voice["train"],
    eval_dataset=common_voice["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)


C:\Users\Santiago\AppData\Local\Temp\ipykernel_3300\2540416661.py:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(


Procedemos a entrenar el modelo, el tiempo de entrenamiento es de 7 horas aproximadamente 

In [38]:
trainer.train()

Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


Due to a bug fix in https://github.com/huggingface/transformers/pull/28687 transcription using a multilingual Whisper will default to language detection followed by transcription instead of translation to English.This might be a breaking change for your use case. If you want to instead always translate your audio to English, make sure to pass `language='en'`.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
C:\Users\Santiago\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.13_qbz5n2kfra8p0\LocalCache\local-packages\Python313\site-packages\transformers\modeling_utils.py:2810: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 448, 'suppress_tokens': [1, 2, 7, 8, 9, 10, 14, 25, 26, 27, 28, 29, 31, 58, 59, 60, 61, 62, 63, 90, 91, 92, 93, 359, 503, 522, 542

TrainOutput(global_step=200, training_loss=1.2177575147151947, metrics={'train_runtime': 25635.643, 'train_samples_per_second': 0.125, 'train_steps_per_second': 0.008, 'total_flos': 9.1654723141632e+17, 'train_loss': 1.2177575147151947, 'epoch': 3.176})

Guardamos el modelo entrenado como un checkpoint para continuar con el entrenamiento.

In [49]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor

# Suponiendo que `trainer` es tu objeto de entrenamiento
model = trainer.model

# Guardar el modelo
model.save_pretrained("C:\\Users\\Santiago\\Desktop\\KeepCoding\\Entrega Practicas\\Entrega-Practica-IA\\Modelofinetuning")

# Crear y guardar el processor (incluye tokenizer y feature extractor)
processor = WhisperProcessor.from_pretrained("openai/whisper-small")
processor.save_pretrained("C:\\Users\\Santiago\\Desktop\\KeepCoding\\Entrega Practicas\\Entrega-Practica-IA\\Modelofinetuning")

[]

Ademas, subimos a Hugging Face el modelo

In [69]:
from huggingface_hub import HfApi

# Crear una instancia de HfApi
api = HfApi()

# Subir la carpeta del modelo a Hugging Face
api.upload_folder(
    folder_path="C:\\Users\\Santiago\\Desktop\\KeepCoding\\Entrega Practicas\\Entrega-Practica-IA\\Modelofinetuning",  # Ruta a la carpeta del modelo
    repo_id="Hewitt2/whisper-small-practica",
    repo_type="model"  # Tipo de repositorio (modelo)
)

CommitInfo(commit_url='https://huggingface.co/Hewitt2/whisper-small-practica/commit/3640b19c1e2b342425c29eb65bbd7366af7967eb', commit_message='Upload folder using huggingface_hub', commit_description='', oid='3640b19c1e2b342425c29eb65bbd7366af7967eb', pr_url=None, repo_url=RepoUrl('https://huggingface.co/Hewitt2/whisper-small-practica', endpoint='https://huggingface.co', repo_type='model', repo_id='Hewitt2/whisper-small-practica'), pr_revision=None, pr_num=None)

Cargamos el modelo (hacemos esto para no tener la necesidad de volver a entrenar)

In [58]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor

# Cargar el modelo guardado
model = WhisperForConditionalGeneration.from_pretrained("C:\\Users\\Santiago\\Desktop\\KeepCoding\\Entrega Practicas\\Entrega-Practica-IA\\Modelofinetuning")

# Cargar el processor (tokenizer y feature extractor)
processor = WhisperProcessor.from_pretrained("C:\\Users\\Santiago\\Desktop\\KeepCoding\\Entrega Practicas\\Entrega-Practica-IA\\Modelofinetuning")

Primeramente, empezamos a comprobar el modelo con un dataset en linea disponible en Hugging Face, para comprobar que tal funciona su entrenamiento.

In [52]:
import torch
from datasets import load_dataset

# Cargar el dataset en modo streaming
dataset = load_dataset("hf-internal-testing/librispeech_asr_dummy", "clean", split="validation", streaming=True)

# Contador para limitar a 10 ejemplos
num_examples = 10
count = 0

# Iterar sobre el dataset en modo streaming
for example in dataset:
    if count >= num_examples:
        break
    
    # Obtener el audio y la transcripción de referencia
    audio = example["audio"]["array"]
    reference_text = example["text"]
    
    # Procesar el audio
    inputs = processor(audio, sampling_rate=16000, return_tensors="pt")
    input_features = inputs.input_features
    
    # Generar transcripción
    with torch.no_grad():
        generated_ids = model.generate(input_features)
    transcription = processor.batch_decode(generated_ids, skip_special_tokens=True)[0]
    
    # Imprimir resultados
    print(f"Ejemplo {count + 1}:")
    print(f"Referencia: {reference_text}")
    print(f"Transcripción: {transcription}")
    print("-" * 50)
    
    count += 1

print("Prueba completada.")

Ejemplo 1:
Referencia: MISTER QUILTER IS THE APOSTLE OF THE MIDDLE CLASSES AND WE ARE GLAD TO WELCOME HIS GOSPEL
Transcripción:  Mr. Quilter is the Apostle of the Middle Classes, and we are glad to welcome his Gospel.
--------------------------------------------------
Ejemplo 2:
Referencia: NOR IS MISTER QUILTER'S MANNER LESS INTERESTING THAN HIS MATTER
Transcripción:  Nor is Mr. Quilter's manner less interesting than his matter.
--------------------------------------------------
Ejemplo 3:
Referencia: HE TELLS US THAT AT THIS FESTIVE SEASON OF THE YEAR WITH CHRISTMAS AND ROAST BEEF LOOMING BEFORE US SIMILES DRAWN FROM EATING AND ITS RESULTS OCCUR MOST READILY TO THE MIND
Transcripción:  He tells us that at this festive season of the year, with Christmas and roast beef looming before us, symbolies drawn from eating and its results occur most readily to the mind.
--------------------------------------------------
Ejemplo 4:
Referencia: HE HAS GRAVE DOUBTS WHETHER SIR FREDERICK LEIGHTON'

Despues, realizamos un analisis mas a detalle con audios de origen propio para verificar la calidad del modelo.

In [68]:
import os
import torchaudio


# Cargar el modelo y el processor
model_path = r"C:\Users\Santiago\Desktop\KeepCoding\Entrega Practicas\Entrega-Practica-IA\Modelofinetuning"
model = WhisperForConditionalGeneration.from_pretrained(model_path)
processor = WhisperProcessor.from_pretrained(model_path)

# Ruta a la carpeta que contiene los archivos de audio
carpeta_audios = r"C:\Users\Santiago\Desktop\KeepCoding\Entrega Practicas\Entrega-Practica-IA\Audios"

# Obtener la lista de archivos en la carpeta
archivos_audio = [f for f in os.listdir(carpeta_audios) if f.endswith(".wav")]

# Procesar cada archivo de audio
for archivo in archivos_audio:
    # Ruta completa al archivo de audio
    audio_path = os.path.join(carpeta_audios, archivo)
    
    print(f"Procesando archivo: {archivo}...")

    # Cargar el archivo de audio
    waveform, sample_rate = torchaudio.load(audio_path)

    # Verificar la tasa de muestreo
    if sample_rate != 16000:
        print(f"Convirtiendo la tasa de muestreo de {sample_rate} Hz a 16000 Hz...")
        resampler = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=16000)
        waveform = resampler(waveform)
        sample_rate = 16000

    # Procesar el audio
    inputs = processor(waveform.squeeze().numpy(), return_tensors="pt", sampling_rate=sample_rate)

    # Realizar la inferencia forzando el idioma español
    with torch.no_grad():
        predicted_ids = model.generate(
            inputs.input_features,
            language="es"  # Forzar el idioma español
        )

    # Decodificar la salida
    transcription = processor.decode(predicted_ids[0], skip_special_tokens=True)
    print(f"Transcripción de {archivo}: {transcription}\n")

Procesando archivo: Audio-de-Whatsapp-1.wav...
Convirtiendo la tasa de muestreo de 48000 Hz a 16000 Hz...
Transcripción de Audio-de-Whatsapp-1.wav:  No creo que tuite las herramientas, las baterías, las máquinas, pese tuito 10 libras.

Procesando archivo: Audio-de-WhatsApp-2.wav...
Convirtiendo la tasa de muestreo de 48000 Hz a 16000 Hz...
Transcripción de Audio-de-WhatsApp-2.wav:  Darásme averiguando del banco voy aquí ya.

Procesando archivo: Audio-de-WhatsApp-3.wav...
Convirtiendo la tasa de muestreo de 48000 Hz a 16000 Hz...
Transcripción de Audio-de-WhatsApp-3.wav:  ¿Qué es, pero que ve que no entiendo?



## Conclusion

En conclusión, el modelo demuestra un rendimiento eficaz al procesar audios de alta calidad, identificando correctamente el idioma y realizando transcripciones precisas. No obstante, al utilizar audios de origen propio, que presentan una calidad inferior y ruido de fondo significativo, se evidencian ciertas limitaciones. En estos casos, es necesario especificar manualmente el idioma para evitar errores en el procesamiento, ya que el modelo tiende a identificar incorrectamente el lenguaje y genera traducciones inexactas. Asimismo, aunque la transcripción no reproduce fielmente las palabras pronunciadas, sí ofrece una comprensión general mejorada del contenido, lo que resulta útil para obtener una idea aproximada del mensaje.

Por lo tanto el modelo se puede decir que el modelo resulta util para traducir mensajes de voz a texto. 